# Задание №1

Есть Pandas DataFrame со столбцами `[“customer_id”, “product_id”, “timestamp”]`, который содержит данные по просмотрам товаров на сайте. Есть проблема – просмотры одного `customer_id` не разбиты на сессии (появления на сайте). Мы хотим разместить сессии так, чтобы сессией считались все смежные просмотры, между которыми не более 3 минут.

Написать методом который создаст в `Pandas DataFrame` столбец `session_id` и проставит в нем уникальный `int id` для каждой сессии.

У каждого пользователя может быть по несколько сессий. Исходный `DataFrame` может быть большим – до 100 млн строк.

# Решение

основные импорты

In [1]:
import pandas as pd
import numpy as np
import datetime
import random
from tqdm import tqdm
import threading
import multiprocessing
from itertools import chain
import glob
import os
from joblib import Parallel, delayed

генерируем массивы уникальных uuid для покупателей и товаров

In [2]:
import uuid

customers = []
max_unique_customers = 100
for _ in range(max_unique_customers):
    customers.append(str(uuid.uuid4()))
    
products = []
max_unique_products = 1000
for _ in range(max_unique_products):
    products.append(uuid.uuid4().hex)

создаем Pandas DataFrame со столбцами [“customer_id”, “product_id”, “timestamp”], который содержит данные по просмотрам товаров на сайте

In [3]:
# однопроцессное решение

# matrix = []
# max_size = 100000000

# dt = datetime.datetime(2022, 9, 1)
# step = datetime.timedelta(seconds=5)

# for _ in tqdm(range(max_size)):
#     matrix.append([random.choice(customers), random.choice(products), dt])
#     dt += step

# многопроцессное решение

def save_part(matrix, id , size):
    columns = ["customer_id", "product_id", "timestamp"]

    df = pd.DataFrame(data=matrix, columns=columns)
    print("Save", "gen_logs"+str(id)+"-"+str(size)+".csv")
    df.to_csv("gen_logs"+str(id)+"-"+str(size)+".csv", index=False, header=True)
    
def gen_matrix_part(id, size):
    # временной интервал между каждым просмотром (просмотры отсортированы по возрастанию даты и времени)
    sec_step = 5
    dt = datetime.datetime(2022, 9, 1) + datetime.timedelta(seconds=sec_step*(id*size))
    step = datetime.timedelta(seconds=sec_step)
    temp_matrix = []
    for i in range(size):
        temp_matrix.append([random.choice(customers), random.choice(products), dt])
        dt += step
    print("Ready job id", id)
    # можно сохранить 10 отдельных файлов (каждый по 10М строк) для условия 100М строк
#     save_part(temp_matrix, id, size)
#     return id
#     или накапливать в оперативной памяти
    return temp_matrix

# procs*size - суммарное число просмотров
procs = 10
size = 100000

# https://superfastpython.com/multiprocessing-pool-map-multiple-arguments/
with multiprocessing.Pool() as pool:
    async_results = [pool.apply_async(gen_matrix_part, args=(i, size,)) for i in range(procs)]
    # close the process pool
    pool.close()
    # wait for all tasks to finish
    pool.join()
    

Ready job id Ready job idReady job id 13 

Ready job id 02

Ready job id 4
Ready job id 5
Ready job id 6
Ready job id 7
Ready job id 8
Ready job id 9


In [4]:
# для случая накопления в оперативной памяти
matrix = [ar.get() for ar in async_results]
# https://stackoverflow.com/a/952952
matrix = list(chain.from_iterable(matrix))

In [5]:
columns = ["customer_id", "product_id", "timestamp"]

df = pd.DataFrame(data=matrix, columns=columns)
df

customer_id  \
0       d2d13aa4-a0a0-44a0-bd90-8b195b401b0b   
1       9aded490-bc8d-43ff-95ff-984a8627e541   
2       a9493b87-d53e-4386-9f71-9bf6e9533b11   
3       f61d9916-a0d9-45ec-9386-7299e4d9efae   
4       139781e5-11e3-46aa-ada3-00e5b2b29356   
...                                      ...   
999995  0e327a91-0854-48ea-954a-2f773f65ef93   
999996  d9234c77-5b7b-424a-90f7-4fce2b90e4d3   
999997  6fd12fff-63ce-42cd-9d82-3323a376c6a8   
999998  d2d13aa4-a0a0-44a0-bd90-8b195b401b0b   
999999  588fad33-34d3-40a6-b413-ef79e9094478   

                              product_id           timestamp  
0       b1627e2baa144f899d32fc35330e3158 2022-09-01 00:00:00  
1       626b1b52034b43bdaae62a793e5b61c1 2022-09-01 00:00:05  
2       f509c916786e440b8638b4ddd8718b55 2022-09-01 00:00:10  
3       0891cba7c05b4ad0963fbeda8fdd3b32 2022-09-01 00:00:15  
4       0aa0771a47c640f59a769f503ea46b64 2022-09-01 00:00:20  
...                                  ...                 ...  
999995  75f7741369c14b9aaee6e421d3d769c4 2022-10-28 20:52:55  
999996  903d367c438c49208d6bb61e52305cdb 2022-10-28 20:53:00  
999997  ad20c17733f6454a9cf6a28257e0e079 2022-10-28 20:53:05  
999998  f2df4b93e63142d2bc76bdb9bac4d2a1 2022-10-28 20:53:10  
999999  4994374de56f4bdea07f8bad85be83af 2022-10-28 20:53:15  

[1000000 rows x 3 columns]

In [6]:
# для случая чтения 10 файлов 
# all_files = glob.glob(os.path.join(".", "*.csv"))
# df = pd.concat((pd.read_csv(f) for f in all_files), ignore_index=True)
# df

проверяем дубликаты для покупателей и продуктов

In [7]:
dups_customer_id = df.pivot_table(columns=['customer_id'], aggfunc='size')
dups_customer_id

customer_id
011e9099-3493-45e9-9f52-bc35193dc1d7     9976
02e0fae0-c986-491d-99d9-d18a901156bc    10028
076dceb5-d026-4fb3-908c-3797d99fc4c6    10060
081b7fcf-e58f-4e31-b9a4-a35ffa8ac662    10006
09ac3eb9-d54b-455c-942e-0fcbfec1b3e5    10057
                                        ...  
f9cac4e7-9d0e-464f-a86f-4cbc81002c7e    10074
fd9105a4-5e6a-44e6-a891-75d816dc0a98     9968
fdd3b593-254f-433e-a956-49d58a871a07    10040
fdd604ee-1373-41a8-904e-519c297604b7    10093
fddf699c-95a0-4809-8c8a-f46b9e809333     9920
Length: 100, dtype: int64

In [8]:
dups_product_id = df.pivot_table(columns=['product_id'], aggfunc='size')
dups_product_id

product_id
0038aaed15934caa88b431e78e4c01fd    1007
005b71f75221496f9a1f2240dc22cdb7    1009
0080e57e9e6b40089c7fb987d1c81e31     970
00912379a85f4d62ae1a33c53daa4bdd     996
00f0245ac4344e63b143798e2bf4ec3e     971
                                    ... 
ff0b16ac076a4873be06f68c088c76bc    1054
ff57b76f116c4faa859f904fca0f3691    1067
ff94b582b3584d648ab8b58ec7579688     996
ff95cd9d2781415d945a308d6039aedf    1009
ffcef1319b32453388332df90fc91404     918
Length: 1000, dtype: int64

пишем функцию добавления сессий

In [9]:
def add_session(group):
    # https://stackoverflow.com/a/41228272
    group['deltaTsec'] = group["timestamp"].diff().dt.seconds.fillna(0).astype(int)
#     print(group)
    
    sessions = []
    session_time = 0
    session_limit = 180
    i = 0
    for delta in group['deltaTsec']:
        session_time += delta
        if i == 0 or session_time > session_limit:
            session_time = 0
            sessions.append(str(uuid.uuid4()))
        elif session_time <= session_limit:
            sessions.append(sessions[i - 1])
        
#         print("session_time",session_time)
        i += 1
        
    group['session_id'] = sessions
    group = group.drop('deltaTsec', axis=1)
#     print(group)
    return group

# однопроцессное решение
# df_groupby = df.groupby("customer_id", as_index=False).apply(add_session)
# df_groupby

In [10]:
# или многопроцессное решение
def applyParallel(dfGrouped, func):
    retLst = Parallel(n_jobs=multiprocessing.cpu_count())(delayed(func)(group) for name, group in dfGrouped)
    return pd.concat(retLst)

df_groupby = applyParallel(df.groupby("customer_id", as_index=False), add_session)

In [11]:
dups_session_id = df_groupby.pivot_table(columns=['session_id'], aggfunc='size')
dups_session_id

session_id
00000a77-28c5-4f3a-b0fb-cc65512087f9    2
000012eb-a0f7-4c4a-83f6-9344849d6805    1
0000194a-da3c-4e5c-ab55-6203f4cade89    1
00001c33-44d8-4426-99cb-c47a91cb2812    5
00005403-6590-4f31-aac2-305014fdda95    3
                                       ..
ffffb5df-6de8-4fc3-9eee-aee89411fb52    1
ffffbef4-0933-42d9-9ffe-7a7268136ad7    1
ffffbf75-44e0-41fb-97fb-eea98f60be7a    1
ffffe9a3-2b4e-4a69-abad-9aac520370da    1
fffff999-4dfd-4d32-8253-51fcf4a1f317    3
Length: 735361, dtype: int64

проверяем, перебирая сессии и проверяя, что разница между первым и последним `timestamp` для уникальной сессии составляет не более 3 минут

In [13]:
def test(session_group):
    print("=====\nДля сессии", session_group.name, 
          "\nпользователя", session_group['customer_id'].iloc[0], 
          "\nразница составляет", session_group['timestamp'].iloc[-1], "-", session_group['timestamp'].iloc[0], "=", session_group['timestamp'].iloc[-1] - session_group['timestamp'].iloc[0], 
          " - ", session_group['timestamp'].iloc[-1] - session_group['timestamp'].iloc[0] <= datetime.timedelta(seconds=180))

df_groupby.groupby("session_id", as_index=False).apply(test)

=====
Для сессии 00000a77-28c5-4f3a-b0fb-cc65512087f9 
пользователя 09ac3eb9-d54b-455c-942e-0fcbfec1b3e5 
разница составляет 2022-09-23 00:33:50 - 2022-09-23 00:31:35 = 0 days 00:02:15  -  True
=====
Для сессии 000012eb-a0f7-4c4a-83f6-9344849d6805 
пользователя 6a13671f-bb0d-4d59-86c4-0cb8b96a58a9 
разница составляет 2022-10-03 22:31:45 - 2022-10-03 22:31:45 = 0 days 00:00:00  -  True
=====
Для сессии 0000194a-da3c-4e5c-ab55-6203f4cade89 
пользователя fd9105a4-5e6a-44e6-a891-75d816dc0a98 
разница составляет 2022-10-09 10:05:30 - 2022-10-09 10:05:30 = 0 days 00:00:00  -  True
=====
Для сессии 00001c33-44d8-4426-99cb-c47a91cb2812 
пользователя c64b2873-b9bd-4796-9e65-2366da5bcca5 
разница составляет 2022-09-19 13:12:50 - 2022-09-19 13:10:15 = 0 days 00:02:35  -  True
=====
Для сессии 00005403-6590-4f31-aac2-305014fdda95 
пользователя 663f99ad-4c1d-4268-885b-4654df6d488e 
разница составляет 2022-09-22 08:29:30 - 2022-09-22 08:27:10 = 0 days 00:02:20  -  True
=====
Для сессии 00006dbc-1a43

=====
Для сессии 00442b16-6640-45dd-93fb-10ca244a2491 
пользователя d9234c77-5b7b-424a-90f7-4fce2b90e4d3 
разница составляет 2022-09-12 02:08:05 - 2022-09-12 02:08:05 = 0 days 00:00:00  -  True
=====
Для сессии 00443de6-12cc-48ba-81b1-128e89104177 
пользователя 8ce76679-dd44-4cba-a228-ba8dc477166f 
разница составляет 2022-10-09 11:04:40 - 2022-10-09 11:04:40 = 0 days 00:00:00  -  True
=====
Для сессии 0044468a-9771-4509-95f0-12dc54764576 
пользователя 081b7fcf-e58f-4e31-b9a4-a35ffa8ac662 
разница составляет 2022-09-07 17:31:10 - 2022-09-07 17:29:25 = 0 days 00:01:45  -  True
=====
Для сессии 004446eb-db53-43f3-bd44-718341b0a4f8 
пользователя c9f18d47-a36c-411c-9aa3-1ef72c9305be 
разница составляет 2022-09-27 21:45:15 - 2022-09-27 21:44:15 = 0 days 00:01:00  -  True
=====
Для сессии 00446343-bd3c-43dd-87ab-c72895ac4563 
пользователя b47d2932-e234-4d3f-a164-f42088d2ebad 
разница составляет 2022-09-18 14:15:50 - 2022-09-18 14:15:50 = 0 days 00:00:00  -  True
=====
Для сессии 004464fa-251f

=====
Для сессии 006cd5ff-9300-4f35-b835-fe4e4ff78ad8 
пользователя f552cee3-9608-4229-82d2-08bca9bc4a5f 
разница составляет 2022-09-06 03:58:55 - 2022-09-06 03:58:55 = 0 days 00:00:00  -  True
=====
Для сессии 006cea6c-78f9-41ce-9d54-141193c06022 
пользователя c278cb86-9f22-4602-ac0c-b3ea4e16baad 
разница составляет 2022-10-11 00:54:55 - 2022-10-11 00:54:55 = 0 days 00:00:00  -  True
=====
Для сессии 006ceb23-8da0-4634-bc54-4554bd6187e7 
пользователя 54fb388a-4255-4be2-96bb-88b784976459 
разница составляет 2022-10-13 14:08:10 - 2022-10-13 14:08:10 = 0 days 00:00:00  -  True
=====
Для сессии 006cfaee-7e2b-4058-a8a1-046346882e50 
пользователя dd1c9a68-22ab-4de8-b3de-92b0c743a0d6 
разница составляет 2022-10-08 21:07:15 - 2022-10-08 21:07:15 = 0 days 00:00:00  -  True
=====
Для сессии 006d2738-0ec2-4ee0-874f-a70763fb525c 
пользователя bf8b0ec1-ce4c-49b9-8787-5cc2512aba59 
разница составляет 2022-09-02 18:35:00 - 2022-09-02 18:35:00 = 0 days 00:00:00  -  True
=====
Для сессии 006d397e-eb8b

=====
Для сессии 00b050b8-2ea2-4891-8fc0-ca189a076278 
пользователя 3a6ae826-56a4-4d38-abfa-701d2db867af 
разница составляет 2022-09-26 07:33:45 - 2022-09-26 07:33:45 = 0 days 00:00:00  -  True
=====
Для сессии 00b09e94-3287-40cd-824d-276d6a93ca3a 
пользователя 240135fc-a841-4dda-bed4-ee0d9103c5ce 
разница составляет 2022-10-14 13:25:10 - 2022-10-14 13:23:50 = 0 days 00:01:20  -  True
=====
Для сессии 00b0a4a3-6ef9-4966-a580-49795be0a621 
пользователя fd9105a4-5e6a-44e6-a891-75d816dc0a98 
разница составляет 2022-10-08 19:49:30 - 2022-10-08 19:49:30 = 0 days 00:00:00  -  True
=====
Для сессии 00b0ab24-c6c0-4851-bae2-3d8339933764 
пользователя c64b2873-b9bd-4796-9e65-2366da5bcca5 
разница составляет 2022-09-20 19:40:25 - 2022-09-20 19:40:25 = 0 days 00:00:00  -  True
=====
Для сессии 00b0ac0a-6425-4062-8894-d012974d90c9 
пользователя 23543b1d-335b-4f27-b7a5-533c8b628758 
разница составляет 2022-10-19 04:12:40 - 2022-10-19 04:12:40 = 0 days 00:00:00  -  True
=====
Для сессии 00b0c994-51a4

=====
Для сессии 013a3163-94f2-4bbe-b5b4-30e41c1497ea 
пользователя e57497a2-e0a6-4124-8bff-9e676c2b0c09 
разница составляет 2022-09-10 01:34:45 - 2022-09-10 01:34:45 = 0 days 00:00:00  -  True
=====
Для сессии 013a4e7a-1193-4f68-945f-efff8275b6f7 
пользователя 5bb45794-de29-48ae-9087-44a7f9100d3c 
разница составляет 2022-09-02 22:50:35 - 2022-09-02 22:50:35 = 0 days 00:00:00  -  True
=====
Для сессии 013a706f-4a52-4899-84bd-0128134dcfe2 
пользователя fddf699c-95a0-4809-8c8a-f46b9e809333 
разница составляет 2022-09-24 05:47:35 - 2022-09-24 05:47:35 = 0 days 00:00:00  -  True
=====
Для сессии 013aa4af-c77e-494f-8ca5-9a3673f76c85 
пользователя dd1c9a68-22ab-4de8-b3de-92b0c743a0d6 
разница составляет 2022-10-23 19:26:45 - 2022-10-23 19:26:45 = 0 days 00:00:00  -  True
=====
Для сессии 013ab318-64c5-473e-854f-be5100980ea0 
пользователя fdd604ee-1373-41a8-904e-519c297604b7 
разница составляет 2022-10-13 09:34:35 - 2022-10-13 09:34:35 = 0 days 00:00:00  -  True
=====
Для сессии 013af088-91e7

...

=====
Для сессии 0730d413-beb7-41e8-8447-275883752bc8 
пользователя 0a751a3f-5e44-4660-8cc3-fcb69095fd09 
разница составляет 2022-09-27 19:12:35 - 2022-09-27 19:12:35 = 0 days 00:00:00  -  True
=====
Для сессии 0730dd3b-d917-4ee6-95f5-629484d7d73b 
пользователя ae02ed9e-d9b4-49b5-836f-9a8bc5ee7e4a 
разница составляет 2022-10-21 02:39:35 - 2022-10-21 02:39:35 = 0 days 00:00:00  -  True
=====
Для сессии 073135b8-c30e-4c7f-9852-2347bc368618 
пользователя 2a93ff89-c3a0-409a-a686-3fd572076d75 
разница составляет 2022-10-21 23:24:40 - 2022-10-21 23:24:40 = 0 days 00:00:00  -  True
=====
Для сессии 07315806-2788-47cc-8b37-53b3ab417ae5 
пользователя 7e4e1819-af2b-4ffa-a099-7c3f2b139ad4 
разница составляет 2022-09-26 21:34:35 - 2022-09-26 21:34:35 = 0 days 00:00:00  -  True
=====
Для сессии 07317d52-7e26-46fe-bef1-3b7ebea0e961 
пользователя 0a751a3f-5e44-4660-8cc3-fcb69095fd09 
разница составляет 2022-09-09 18:39:40 - 2022-09-09 18:39:40 = 0 days 00:00:00  -  True
=====
Для сессии 073189f9-9e0f

=====
Для сессии 075a6150-a2ba-41ea-afd5-f124bd1d6982 
пользователя 489bd57b-14f9-4b8c-a614-e4ac6779d902 
разница составляет 2022-10-17 09:35:30 - 2022-10-17 09:35:30 = 0 days 00:00:00  -  True
=====
Для сессии 075a6908-a14a-4f3d-bba6-9e68d66a3495 
пользователя 97f51e8e-4ba9-468b-b5c8-0aeb6ae0bb77 
разница составляет 2022-09-06 01:15:05 - 2022-09-06 01:15:05 = 0 days 00:00:00  -  True
=====
Для сессии 075a7006-813d-4432-a2e3-404643170aba 
пользователя bc44861c-694b-440b-bdec-159ad622664a 
разница составляет 2022-10-19 09:19:10 - 2022-10-19 09:17:15 = 0 days 00:01:55  -  True
=====
Для сессии 075a7171-778d-40ad-a7be-686fb0dad912 
пользователя 663f99ad-4c1d-4268-885b-4654df6d488e 
разница составляет 2022-10-03 18:46:15 - 2022-10-03 18:46:15 = 0 days 00:00:00  -  True
=====
Для сессии 075a8203-ddf3-4ecc-90ce-a3f06204c178 
пользователя 87af0469-5e79-4e25-ba6b-e9f2a9bbebab 
разница составляет 2022-09-08 03:44:50 - 2022-09-08 03:44:50 = 0 days 00:00:00  -  True
=====
Для сессии 075a92ca-bfa3

=====
Для сессии 078a84f9-140f-45d2-a907-3fd42dcb1d91 
пользователя fdd3b593-254f-433e-a956-49d58a871a07 
разница составляет 2022-09-01 05:08:55 - 2022-09-01 05:08:30 = 0 days 00:00:25  -  True
=====
Для сессии 078a988b-8cad-41da-b267-7615fac50b83 
пользователя 2a3d9e1a-1781-4833-ad34-32628e112e26 
разница составляет 2022-10-14 23:30:55 - 2022-10-14 23:30:55 = 0 days 00:00:00  -  True
=====
Для сессии 078aa6f0-bf19-4074-bb6e-ba278be745b1 
пользователя ce033c53-8eba-41a4-84ac-fa87b96ab014 
разница составляет 2022-10-04 21:56:05 - 2022-10-04 21:56:05 = 0 days 00:00:00  -  True
=====
Для сессии 078ab74c-dbf3-4991-90db-a64b4280c92c 
пользователя e18156ed-61a0-4367-b15c-95f28bbcdc34 
разница составляет 2022-10-25 16:29:25 - 2022-10-25 16:29:25 = 0 days 00:00:00  -  True
=====
Для сессии 078ac1a8-530b-4663-9a2c-92e787cab04b 
пользователя 98bd8cfb-6ebb-4bf0-8579-5d6728c316dd 
разница составляет 2022-09-26 05:49:40 - 2022-09-26 05:49:40 = 0 days 00:00:00  -  True
=====
Для сессии 078ae0a4-29bd

=====
Для сессии 07c0764e-37c3-47f7-8048-807135d634d5 
пользователя a9493b87-d53e-4386-9f71-9bf6e9533b11 
разница составляет 2022-10-12 18:15:15 - 2022-10-12 18:15:15 = 0 days 00:00:00  -  True
=====
Для сессии 07c07a48-3796-4cf2-b41a-7cb09f76e36a 
пользователя f09be174-a0df-4e12-9d10-75a3fe2f9ea1 
разница составляет 2022-10-22 20:22:55 - 2022-10-22 20:20:55 = 0 days 00:02:00  -  True
=====
Для сессии 07c08008-ba29-4084-87fb-1bc9d3f317ab 
пользователя d5ce928e-b984-40cf-a68a-84e186a74390 
разница составляет 2022-09-18 13:28:05 - 2022-09-18 13:28:05 = 0 days 00:00:00  -  True
=====
Для сессии 07c0e4b4-044a-4715-8ca7-4545c74f5b3f 
пользователя 64547be7-ee83-49de-a17b-a5bbf85cac13 
разница составляет 2022-09-16 20:44:05 - 2022-09-16 20:44:05 = 0 days 00:00:00  -  True
=====
Для сессии 07c0fa70-6453-4903-ba60-c972b1d113df 
пользователя fdd3b593-254f-433e-a956-49d58a871a07 
разница составляет 2022-09-06 04:54:05 - 2022-09-06 04:54:05 = 0 days 00:00:00  -  True
=====
Для сессии 07c11cc1-f522

KeyboardInterrupt: 

In [ ]:
df.loc[df['customer_id'] == "6b8b38d2-8e56-4a56-a806-f87e4789d0e8"]

In [ ]:
df[:20]